<a href="https://colab.research.google.com/github/SpandanaKalakonda/Building_ML_Pipelines/blob/main/data_validation_using_tf.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install tfx --quiet

In [2]:
!pip install apache-beam --quiet

In [3]:
!git clone https://github.com/Building-ML-Pipelines/building-machine-learning-pipelines.git

Cloning into 'building-machine-learning-pipelines'...
remote: Enumerating objects: 801, done.
remote: Counting objects: 100% (130/130), done.
remote: Compressing objects: 100% (38/38), done.
remote: Total 801 (delta 104), reused 92 (delta 92), pack-reused 671
Receiving objects: 100% (801/801), 29.35 MiB | 12.92 MiB/s, done.
Resolving deltas: 100% (433/433), done.


In [4]:
%cd building-machine-learning-pipelines/
!python3 utils/download_dataset.py
%cd ..

/content/building-machine-learning-pipelines
INFO:root:Started download script
INFO:root:Data folder created.
INFO:urllib3.poolmanager:Redirecting http://bit.ly/building-ml-pipelines-dataset -> https://drive.google.com/uc?export=download&id=1VHjb8L8n2d6eLz_lA-F-bk6Z0UecHpEF
INFO:urllib3.poolmanager:Redirecting https://drive.google.com/uc?export=download&id=1VHjb8L8n2d6eLz_lA-F-bk6Z0UecHpEF -> https://doc-0o-8s-docs.googleusercontent.com/docs/securesc/ha0ro937gcuc7l7deffksulhg5h7mbp1/ajvmocrb8kaljis4sk4v5jbt5dfudt1k/1703033025000/06616860426990197454/*/1VHjb8L8n2d6eLz_lA-F-bk6Z0UecHpEF?e=download&uuid=b1c7e666-0485-4aeb-a132-218a467cc075
INFO:root:Download completed.
INFO:root:Finished download script
/content


In [42]:
import tensorflow_data_validation as tfdv
import csv
import tensorflow as tf
from tqdm import tqdm
from tensorflow_data_validation.utils import slicing_util

**Generating the statistics of the csv data**

In [6]:
stats = tfdv.generate_statistics_from_csv(
    data_location='/content/building-machine-learning-pipelines/data/consumer_complaints_with_narrative.csv',
    delimiter=','
    )

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


**Visualizing the statistics**

In [7]:
tfdv.visualize_statistics(stats)

**Generating Schema from the Data**

In [8]:
schema = tfdv.infer_schema(stats)

In [9]:
schema

feature {
  name: "product"
  type: BYTES
  domain: "product"
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "sub_product"
  value_count {
    min: 1
    max: 1
  }
  type: BYTES
  domain: "sub_product"
  presence {
    min_count: 1
  }
}
feature {
  name: "issue"
  type: BYTES
  domain: "issue"
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "sub_issue"
  value_count {
    min: 1
    max: 1
  }
  type: BYTES
  domain: "sub_issue"
  presence {
    min_count: 1
  }
}
feature {
  name: "consumer_complaint_narrative"
  type: BYTES
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "company"
  type: BYTES
  presence {
    min_fraction: 1.0
    min_count: 1
  }
  shape {
    dim {
      size: 1
    }
  }
}
feature {
  name: "state"
  value_count {
    min: 1
    max: 1
  }
  type:

In [10]:
#display the schema
tfdv.display_schema(schema)

Type  Presence Valency              Domain
Feature name                                                                
'product'                       STRING  required                   'product'
'sub_product'                   STRING  optional  single       'sub_product'
'issue'                         STRING  required                     'issue'
'sub_issue'                     STRING  optional  single         'sub_issue'
'consumer_complaint_narrative'   BYTES  required                           -
'company'                        BYTES  required                           -
'state'                         STRING  optional  single             'state'
'zip_code'                       BYTES  optional  single                   -
'company_response'              STRING  required          'company_response'
'timely_response'               STRING  required           'timely_response'
'consumer_disputed'                INT  required                           -

Values
Domain                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
'product'                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            

Saving the Schema to File

In [11]:
# Save the schema to a file
tfdv.write_schema_text(schema, 'schema_csv.pbtxt')

Converting the CSV file to TF Record

In [12]:
def _bytes_feature(value):
  return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value.encode()]))
def _int64_feature(value):
  return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))

In [13]:
def clean_rows(row):
  if not row["zip_code"]:
    row["zip_code"] = "99999"
  return row

In [14]:
def convert_zipcode_to_int(zipcode):
  if isinstance(zipcode, str) and "XX" in zipcode:
    zipcode = zipcode.replace("XX", "00")
  int_zipcode = int(zipcode)
  return int_zipcode

In [15]:
original_data_file = "/content/building-machine-learning-pipelines/data/consumer_complaints_with_narrative.csv"
tfrecord_filename = "consumer_complaints.tfrecord"
tf_record_writer = tf.io.TFRecordWriter(tfrecord_filename)

In [16]:
with open(original_data_file) as csv_file:
  reader = csv.DictReader(csv_file, delimiter=",", quotechar='"')
  for row in tqdm(reader):
    row = clean_rows(row)
    example = tf.train.Example(
        features=tf.train.Features(
            feature={
                "product": _bytes_feature(row["product"]),
                "sub_product": _bytes_feature(row["sub_product"]),
                "issue": _bytes_feature(row["issue"]),
                "sub_issue": _bytes_feature(row["sub_issue"]),
                "state": _bytes_feature(row["state"]),
                "zip_code": _int64_feature(convert_zipcode_to_int(row["zip_code"])),
                "company": _bytes_feature(row["company"]),
                "company_response": _bytes_feature(row["company_response"]),
                "consumer_complaint_narrative": _bytes_feature(row["consumer_complaint_narrative"]),
                "timely_response": _bytes_feature(row["timely_response"]),
                "consumer_disputed": _bytes_feature(row["consumer_disputed"]),
            }
        )
        )
    tf_record_writer.write(example.SerializeToString())
  tf_record_writer.close()

66799it [00:10, 6544.34it/s]


Generating and Visualizing the statistics of TFRecord data


In [17]:
stats_tf_record = tfdv.generate_statistics_from_tfrecord(
    data_location='/content/consumer_complaints.tfrecord'
)

In [18]:
tfdv.visualize_statistics(stats_tf_record)

Generating the schema of TFRecord data

In [19]:
schema_tf_record = tfdv.infer_schema(stats_tf_record)

In [20]:
tfdv.display_schema(schema_tf_record)

Type  Presence Valency              Domain
Feature name                                                                
'company'                        BYTES  required                           -
'company_response'              STRING  required          'company_response'
'consumer_complaint_narrative'   BYTES  required                           -
'consumer_disputed'              BYTES  required                           -
'issue'                         STRING  required                     'issue'
'product'                       STRING  required                   'product'
'state'                         STRING  required                     'state'
'sub_issue'                     STRING  required                 'sub_issue'
'sub_product'                   STRING  required               'sub_product'
'timely_response'               STRING  required           'timely_response'
'zip_code'                         INT  required                           -

Values
Domain                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             
'company_response'                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   

In [21]:
# Save the schema to a file
tfdv.write_schema_text(schema_tf_record, 'schema_tf_record.pbtxt')

**Comparing the statistics of CSV Data and TFRecord data**

In [22]:
tfdv.visualize_statistics(lhs_statistics=stats, rhs_statistics=stats_tf_record,
                          lhs_name="CSV Dataset", rhs_name="TF RECORD Dataset")

**Identifying the anamolies in the data comparing against the Schema of training data**

In [23]:
anamolies = tfdv.validate_statistics(statistics=stats, schema=schema_tf_record)

In [24]:
tfdv.display_anomalies(anamolies)

Anomaly short description  \
Feature name                                    
'zip_code'                    Multiple errors   
'state'                       Multiple errors   
'sub_issue'                   Multiple errors   
'sub_product'                 Multiple errors   
'consumer_disputed'      Unexpected data type   

                                                                                                                                                                                                                                                                                                                Anomaly long description  
Feature name                                                                                                                                                                                                                                                                                                                              
'zip_code'           The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.997171 Expected data of type: INT but got STRING  
'state'                                                        The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.997216  
'sub_issue'                                                    The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.492986  
'sub_product'                                                  The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.693828  
'consumer_disputed'                                                                                                                                                                                                                                                                             Expected data of type: BYTES but got INT

In [25]:
anamolies

baseline {
  feature {
    name: "company"
    type: BYTES
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "company_response"
    type: BYTES
    domain: "company_response"
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "consumer_complaint_narrative"
    type: BYTES
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "consumer_disputed"
    type: BYTES
    bool_domain {
      true_value: "1"
      false_value: "0"
    }
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1
      }
    }
  }
  feature {
    name: "issue"
    type: BYTES
    domain: "issue"
    presence {
      min_fraction: 1.0
      min_count: 1
    }
    shape {
      dim {
        size: 1

In [63]:
#loading the schema from file
schema_tf = tfdv.load_schema_text("/content/schema_tf_record.pbtxt")

In [27]:
type(schema_tf)

tensorflow_metadata.proto.v0.schema_pb2.Schema

**Updating the schema by removing a state "AK"**

In [28]:
sub_issue_feature = tfdv.get_feature(schema_tf, 'sub_issue')
sub_issue_feature.presence.min_fraction = 0.9

In [29]:
state_domain = tfdv.get_domain(schema_tf, 'state')

In [30]:
state_domain

name: "state"
value: ""
value: "AA"
value: "AE"
value: "AK"
value: "AL"
value: "AP"
value: "AR"
value: "AS"
value: "AZ"
value: "CA"
value: "CO"
value: "CT"
value: "DC"
value: "DE"
value: "FL"
value: "FM"
value: "GA"
value: "GU"
value: "HI"
value: "IA"
value: "ID"
value: "IL"
value: "IN"
value: "KS"
value: "KY"
value: "LA"
value: "MA"
value: "MD"
value: "ME"
value: "MI"
value: "MN"
value: "MO"
value: "MP"
value: "MS"
value: "MT"
value: "NC"
value: "ND"
value: "NE"
value: "NH"
value: "NJ"
value: "NM"
value: "NV"
value: "NY"
value: "OH"
value: "OK"
value: "OR"
value: "PA"
value: "PR"
value: "RI"
value: "SC"
value: "SD"
value: "TN"
value: "TX"
value: "UT"
value: "VA"
value: "VI"
value: "VT"
value: "WA"
value: "WI"
value: "WV"
value: "WY"

In [31]:
state_domain.value.remove('AK')

In [32]:
state_domain

name: "state"
value: ""
value: "AA"
value: "AE"
value: "AL"
value: "AP"
value: "AR"
value: "AS"
value: "AZ"
value: "CA"
value: "CO"
value: "CT"
value: "DC"
value: "DE"
value: "FL"
value: "FM"
value: "GA"
value: "GU"
value: "HI"
value: "IA"
value: "ID"
value: "IL"
value: "IN"
value: "KS"
value: "KY"
value: "LA"
value: "MA"
value: "MD"
value: "ME"
value: "MI"
value: "MN"
value: "MO"
value: "MP"
value: "MS"
value: "MT"
value: "NC"
value: "ND"
value: "NE"
value: "NH"
value: "NJ"
value: "NM"
value: "NV"
value: "NY"
value: "OH"
value: "OK"
value: "OR"
value: "PA"
value: "PR"
value: "RI"
value: "SC"
value: "SD"
value: "TN"
value: "TX"
value: "UT"
value: "VA"
value: "VI"
value: "VT"
value: "WA"
value: "WI"
value: "WV"
value: "WY"

**Update the schema of the saved schema file and identify the anomolies after updating the Schema**

In [33]:
tfdv.write_schema_text(schema_tf, "/content/schema_tf_record.pbtxt")

In [34]:
updated_anomalies = tfdv.validate_statistics(statistics=stats, schema=schema_tf)

In [35]:
tfdv.display_anomalies(updated_anomalies)

Anomaly short description  \
Feature name                                    
'sub_product'                 Multiple errors   
'state'                       Multiple errors   
'zip_code'                    Multiple errors   
'sub_issue'                   Multiple errors   
'consumer_disputed'      Unexpected data type   

                                                                                                                                                                                                                                                                                                                                  Anomaly long description  
Feature name                                                                                                                                                                                                                                                                                                                                                
'sub_product'                                                                    The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.693828  
'state'              The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.997216 Examples contain values missing from the schema: AK (<1%).   
'zip_code'                             The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.997171 Expected data of type: INT but got STRING  
'sub_issue'                                                                      The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 0.900000, actual = 0.492986  
'consumer_disputed'                                                                                                                                                                                                                                                                                               Expected data of type: BYTES but got INT

**Data Skewness and Drift**

In [36]:
tfdv.get_feature(schema_tf, 'zip_code').skew_comparator.infinity_norm.threshold = 0.01
skew_anomalies = tfdv.validate_statistics(statistics=stats, schema=schema_tf, serving_statistics=stats_tf_record)

In [37]:
tfdv.display_anomalies(skew_anomalies)

Anomaly short description  \
Feature name                                    
'sub_product'                 Multiple errors   
'zip_code'                    Multiple errors   
'state'                       Multiple errors   
'consumer_disputed'      Unexpected data type   
'sub_issue'                   Multiple errors   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            Anomaly long description  
Feature name                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          
'sub_product'                                                                                                                                                                                                                              The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.693828  
'zip_code'           The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.997171 Expected data of type: INT but got STRING The Linfty distance between training and serving is 0.0154031 (up to six significant digits), above the threshold 0.01. The feature value with maximum difference is: 300XX  
'state'                                                                                                                                                                        The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 1.000000, actual = 0.997216 Examples contain values missing from the schema: AK (<1%).   
'consumer_disputed'                                                                                                                                                                                                                                                                                                                                                                                                                                                         Expected data of type: BYTES but got INT  
'sub_issue'                                                                                                                                                                                                                                The feature has a shape, but it's not always present (if the feature is nested, then it should always be present at each nested level) or its value lengths vary. The feature was present in fewer examples than expected: minimum fraction = 0.900000, actual = 0.492986

In [38]:
tfdv.get_feature(schema_tf, 'sub_issue').drift_comparator.infinity_norm.threshold = 0.01
drift_anomalies = tfdv.validate_statistics(previous_statistics=stats, schema=schema_tf, statistics=stats_tf_record)

In [39]:
tfdv.display_anomalies(drift_anomalies)

Anomaly short description  \
Feature name                                                      
'sub_issue'   High Linfty distance between current and previous   
'state'                                Unexpected string values   

                                                                                                                                                           Anomaly long description  
Feature name                                                                                                                                                                         
'sub_issue'   The Linfty distance between current and previous is 0.507014 (up to six significant digits), above the threshold 0.01. The feature value with maximum difference is:   
'state'                                                                                                                 Examples contain values missing from the schema: AK (<1%).

**Slicing the data on Feature values**

In [43]:
slice_fn1 = slicing_util.get_feature_value_slicer(
    features={'state':[b'CA']} # feature value as a list of binary values
)
slice_options = tfdv.StatsOptions(slice_functions=[slice_fn1])
slice_stats = tfdv.generate_statistics_from_csv(
    data_location='/content/building-machine-learning-pipelines/data/consumer_complaints_with_narrative.csv',
    stats_options=slice_options
)

/usr/local/lib/python3.10/dist-packages/tensorflow_data_validation/utils/slicing_util.py:183: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  merged_df[_SLICE_KEY_COLUMN] = ''
/usr/local/lib/python3.10/dist-packages/tensorflow_data_validation/utils/slicing_util.py:193: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  merged_df[_SLICE_KEY_COLUMN] = slice_key_col


In [71]:
from tensorflow_metadata.proto.v0 import statistics_pb2

def display_slice_keys(stats):
  print(list(map(lambda x:x.name, slice_stats.datasets)))

def get_sliced_stats(stats, slice_key):
  for sliced_stats in stats.datasets:
    if sliced_stats.name == slice_key:
      result = statistics_pb2.DatasetFeatureStatisticsList()
      result.datasets.add().CopyFrom(sliced_stats)
      return result
    print('Invalid Slice Key')
def compare_slices(stats, slice_key1, slice_key2):
  lhs_stats = get_sliced_stats(stats, slice_key1)
  rhs_stats = get_sliced_stats(stats, slice_key2)
  tfdv.visualize_statistics(lhs_stats, rhs_stats)

In [48]:
tfdv.visualize_statistics(get_sliced_stats(slice_stats, 'state_CA'))

Invalid Slice Key


In [60]:
tfdv.visualize_statistics(get_sliced_stats(slice_stats, 'state_CA'))

Invalid Slice Key


In [ ]:
compare_slices(slice_stats, 'state_CA', 'All Examples')